In [5]:
# pandas for building and processing DataFrames
%pip install pandas

# sqlalchemy: database toolkit for Python (ORM)
%pip install sqlalchemy

# pandasql: sql-type queries on pandas DataFrames
%pip install pandasql


Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [ ]:
# API example

import requests
from json import dumps

# API key for the Open Movie Database (OMDb)
api_key = "dcbd4e7e"
movie_id = "tt3896198"  # Example IMDb ID
url = f"http://www.omdbapi.com/?i={movie_id}&apikey={api_key}"

response = requests.get(url)
movie_data = response.json()

# Print the data to inspect the fields
print(movie_data)



{'Title': 'Guardians of the Galaxy Vol. 2', 'Year': '2017', 'Rated': 'PG-13', 'Released': '05 May 2017', 'Runtime': '136 min', 'Genre': 'Action, Adventure, Comedy', 'Director': 'James Gunn', 'Writer': 'James Gunn, Dan Abnett, Andy Lanning', 'Actors': 'Chris Pratt, Zoe Saldaña, Dave Bautista', 'Plot': "The Guardians struggle to keep together as a team while dealing with their personal family issues, notably Star-Lord's encounter with his father, the ambitious celestial being Ego.", 'Language': 'English', 'Country': 'United States', 'Awards': 'Nominated for 1 Oscar. 15 wins & 61 nominations total', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNWE5MGI3MDctMmU5Ni00YzI2LWEzMTQtZGIyZDA5MzQzNDBhXkEyXkFqcGc@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '7.6/10'}, {'Source': 'Rotten Tomatoes', 'Value': '85%'}, {'Source': 'Metacritic', 'Value': '67/100'}], 'Metascore': '67', 'imdbRating': '7.6', 'imdbVotes': '788,570', 'imdbID': 'tt3896198', 'Type': 'movie', '

In [ ]:
import sqlite3

conn = sqlite3.connect("../models/cinemind.db")
cursor = conn.cursor()

# SQL code to create the Movie_Genre table
create_table_sql = """
CREATE TABLE Movie_Genre (
    movie_id INTEGER NOT NULL,        -- References the id from the Movies table
    genre_id INTEGER NOT NULL,        -- References the genre_id from the Genres table
    PRIMARY KEY (movie_id, genre_id)  -- Composite primary key
);
"""

conn.commit()
conn.close()

In [ ]:
import sqlite3
import pandas as pd
import json

# Connect to SQLite database
conn = sqlite3.connect('../models/cinemind.db')  # Use your database path
cursor = conn.cursor()

# Read the CSV using pandas
df = pd.read_csv('../data/tmdb_5000_movies.csv')

# Function to insert into the Movies table
def insert_movie(row):
    cursor.execute('''
        INSERT INTO Movies (id, title, overview, release_date, budget, revenue, runtime, popularity, original_language, original_title, homepage, status, tagline, vote_average, vote_count)
        VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
    ''', (
        row['id'], row['title'], row['overview'], row['release_date'], row['budget'], row['revenue'], 
        row['runtime'], row['popularity'], row['original_language'], row['original_title'], 
        row['homepage'], row['status'], row['tagline'], row['vote_average'], row['vote_count']
    ))

# Function to insert genres into the Genres table and link with Movie_Genre
def insert_genres(movie_id, genres_json):
    genres = json.loads(genres_json)
    for genre in genres:
        genre_name = genre['name']
        
        # Check if genre exists, if not, insert
        cursor.execute('SELECT genre_id FROM Genres WHERE genre_name = ?', (genre_name,))
        result = cursor.fetchone()
        
        if result:
            genre_id = result[0]
        else:
            cursor.execute('INSERT INTO Genres (genre_name) VALUES (?)', (genre_name,))
            genre_id = cursor.lastrowid
        
        # Link genre with movie in Movie_Genre
        cursor.execute('''
            INSERT OR IGNORE INTO Movie_Genre (movie_id, genre_id)
            VALUES (?, ?)
        ''', (movie_id, genre_id))

# Function to insert keywords into the Keywords table and link with Movie_Keywords
def insert_keywords(movie_id, keywords_json):
    keywords = json.loads(keywords_json)
    for keyword in keywords:
        keyword_name = keyword['name']
        
        # Check if keyword exists, if not, insert
        cursor.execute('SELECT keyword_id FROM Keywords WHERE keyword_name = ?', (keyword_name,))
        result = cursor.fetchone()
        
        if result:
            keyword_id = result[0]
        else:
            cursor.execute('INSERT INTO Keywords (keyword_name) VALUES (?)', (keyword_name,))
            keyword_id = cursor.lastrowid
        
        # Link keyword with movie in Movie_Keywords
        cursor.execute('''
            INSERT OR IGNORE INTO Movie_Keywords (movie_id, keyword_id)
            VALUES (?, ?)
        ''', (movie_id, keyword_id))

# Function to insert spoken languages into the Spoken_Languages table and link with Movie_Spoken_Languages
def insert_languages(movie_id, languages_json):
    languages = json.loads(languages_json)
    for language in languages:
        language_name = language['name']
        
        # Check if language exists, if not, insert
        cursor.execute('SELECT language_id FROM Spoken_Languages WHERE language_name = ?', (language_name,))
        result = cursor.fetchone()
        
        if result:
            language_id = result[0]
        else:
            cursor.execute('INSERT INTO Spoken_Languages (language_name) VALUES (?)', (language_name,))
            language_id = cursor.lastrowid
        
        # Link language with movie in Movie_Spoken_Languages
        cursor.execute('''
            INSERT OR IGNORE INTO Movie_Spoken_Languages (movie_id, language_id)
            VALUES (?, ?)
        ''', (movie_id, language_id))

# Iterate through the CSV and insert data into tables
for _, row in df.iterrows():
    # Insert movie data
    insert_movie(row)
    
    # Insert genres
    insert_genres(row['id'], row['genres'])
    
    # Insert keywords
    insert_keywords(row['id'], row['keywords'])
    
    # Insert spoken languages
    insert_languages(row['id'], row['spoken_languages'])

# Commit changes to the database
conn.commit()

# Close the connection
conn.close()

print("Data inserted successfully!")


Data inserted successfully!


In [ ]:
import sqlite3
import pandas as pd
import json

# Connect to SQLite database
conn = sqlite3.connect('../models/cinemind.db')  # Update path if needed
cursor = conn.cursor()

print("Connected to database.")

# Read the CSV using pandas
print("Reading credits CSV file...")
df_credits = pd.read_csv('../data/tmdb_5000_credits.csv')
print(f"Total records in credits file: {len(df_credits)}")

# Function to insert actors into the Cast table
def insert_actor(actor_name, gender):
    cursor.execute('SELECT actor_id FROM Cast WHERE name = ?', (actor_name,))
    result = cursor.fetchone()

    if result:
        actor_id = result[0]
        print(f"  Actor '{actor_name}' already exists with ID {actor_id}.")
    else:
        cursor.execute('INSERT INTO Cast (name, gender) VALUES (?, ?)', (actor_name, gender))
        actor_id = cursor.lastrowid  # Get the newly inserted actor_id
        print(f"  Inserted new actor: {actor_name} (ID: {actor_id}, Gender: {gender})")
    
    return actor_id

# Function to insert first 10 cast members into Movies_Cast table
def insert_movie_cast(movie_id, cast_json):
    try:
        cast_list = json.loads(cast_json)[:10]  # Limit to first 10 cast members
    except json.JSONDecodeError as e:
        print(f"Error decoding JSON for movie_id {movie_id}: {e}")
        return
    
    print(f"\nProcessing movie_id {movie_id}: {len(cast_list)} cast members (limited to 10).")

    for i, cast_member in enumerate(cast_list):
        actor_name = cast_member['name']
        gender = cast_member.get('gender', 0)  # Default to 0 if missing
        character = cast_member.get('character', 'Unknown')

        # Insert into Cast table and get actor_id
        actor_id = insert_actor(actor_name, gender)

        # Insert into Movies_Cast table
        cursor.execute('''
            INSERT OR IGNORE INTO Movies_Cast (movie_id, actor_id, character)
            VALUES (?, ?, ?)
        ''', (movie_id, actor_id, character))

        print(f"    ({i+1}/10) Linked {actor_name} (ID: {actor_id}) to movie {movie_id} as '{character}'")

# Iterate through the credits CSV and insert data
for idx, row in df_credits.iterrows():
    print(f"\n[{idx+1}/{len(df_credits)}] Processing movie: {row['movie_id']}...")
    insert_movie_cast(row['movie_id'], row['cast'])

    # Commit every 100 movies to prevent large transactions slowing down
    if (idx + 1) % 100 == 0:
        conn.commit()
        print("Committed to database after 100 movies.")

# Final commit to the database
conn.commit()
print("Final commit completed.")

# Close the connection
conn.close()
print("Database connection closed.")

print("Cast data inserted successfully!")


Connected to database.
Reading credits CSV file...
Total records in credits file: 4803

[1/4803] Processing movie: 19995...

Processing movie_id 19995: 10 cast members (limited to 10).
  Actor 'Sam Worthington' already exists with ID 1.
    (1/10) Linked Sam Worthington (ID: 1) to movie 19995 as 'Jake Sully'
  Actor 'Zoe Saldana' already exists with ID 2.
    (2/10) Linked Zoe Saldana (ID: 2) to movie 19995 as 'Neytiri'
  Actor 'Sigourney Weaver' already exists with ID 3.
    (3/10) Linked Sigourney Weaver (ID: 3) to movie 19995 as 'Dr. Grace Augustine'
  Actor 'Stephen Lang' already exists with ID 4.
    (4/10) Linked Stephen Lang (ID: 4) to movie 19995 as 'Col. Quaritch'
  Actor 'Michelle Rodriguez' already exists with ID 5.
    (5/10) Linked Michelle Rodriguez (ID: 5) to movie 19995 as 'Trudy Chacon'
  Actor 'Giovanni Ribisi' already exists with ID 6.
    (6/10) Linked Giovanni Ribisi (ID: 6) to movie 19995 as 'Selfridge'
  Actor 'Joel David Moore' already exists with ID 7.
    (7/1

In [ ]:
import sqlite3
import pandas as pd
import json

# Connect to SQLite database
conn = sqlite3.connect('../models/cinemind.db')  # Update path if needed
cursor = conn.cursor()

print("Connected to database.")

# Read the CSV using pandas
print("Reading movies CSV file...")
df_movies = pd.read_csv('../data/tmdb_5000_movies.csv')
print(f"Total records in movies file: {len(df_movies)}")

# Function to insert production country
def insert_production_country(iso_code, country_name):
    cursor.execute('SELECT country_id FROM Production_Countries WHERE iso_code = ?', (iso_code,))
    result = cursor.fetchone()

    if result:
        country_id = result[0]
        print(f"  Country '{country_name}' ({iso_code}) already exists with ID {country_id}.")
    else:
        cursor.execute('INSERT INTO Production_Countries (iso_code, country_name) VALUES (?, ?)', (iso_code, country_name))
        country_id = cursor.lastrowid  # Get the newly inserted country_id
        print(f"  Inserted new country: {country_name} (ID: {country_id}, ISO: {iso_code})")
    
    return country_id

# Function to insert production countries for a movie
def insert_movie_production_countries(movie_id, production_countries_json):
    try:
        country_list = json.loads(production_countries_json)  # Parse JSON string
    except json.JSONDecodeError as e:
        print(f"Error decoding JSON for movie_id {movie_id}: {e}")
        return
    
    print(f"\nProcessing movie_id {movie_id}: {len(country_list)} production countries.")

    for country in country_list:
        iso_code = country.get('iso_3166_1', 'Unknown')
        country_name = country.get('name', 'Unknown')

        # Insert into Production_Countries table and get country_id
        country_id = insert_production_country(iso_code, country_name)

        # Insert into Movie_Production_Countries table
        cursor.execute('''
            INSERT OR IGNORE INTO Movie_Production_Countries (movie_id, country_id)
            VALUES (?, ?)
        ''', (movie_id, country_id))

        print(f"    Linked {country_name} (ID: {country_id}) to movie {movie_id}.")

# Iterate through the movies CSV and insert production country data
for idx, row in df_movies.iterrows():
    print(f"\n[{idx+1}/{len(df_movies)}] Processing movie: {row['id']} - {row['title']}...")
    insert_movie_production_countries(row['id'], row['production_countries'])

    # Commit every 100 movies to prevent large transactions slowing down
    if (idx + 1) % 100 == 0:
        conn.commit()
        print("Committed to database after 100 movies.")

# Final commit to the database
conn.commit()
print("Final commit completed.")

# Close the connection
conn.close()
print("Database connection closed.")

print("Production countries inserted successfully!")


Connected to database.
Reading movies CSV file...
Total records in movies file: 4803

[1/4803] Processing movie: 19995 - Avatar...

Processing movie_id 19995: 2 production countries.
  Inserted new country: United States of America (ID: 1, ISO: US)
    Linked United States of America (ID: 1) to movie 19995.
  Inserted new country: United Kingdom (ID: 2, ISO: GB)
    Linked United Kingdom (ID: 2) to movie 19995.

[2/4803] Processing movie: 285 - Pirates of the Caribbean: At World's End...

Processing movie_id 285: 1 production countries.
  Country 'United States of America' (US) already exists with ID 1.
    Linked United States of America (ID: 1) to movie 285.

[3/4803] Processing movie: 206647 - Spectre...

Processing movie_id 206647: 2 production countries.
  Country 'United Kingdom' (GB) already exists with ID 2.
    Linked United Kingdom (ID: 2) to movie 206647.
  Country 'United States of America' (US) already exists with ID 1.
    Linked United States of America (ID: 1) to movie 